In [90]:
pwd()

"C:\\Users\\Jordan\\AppData\\Local\\Julia-0.4.0-32"

In [ ]:
Pkg.test("Toms566")

In [3]:
using Toms566
using ReverseDiffSource

In [70]:
function newtmin_tom(p, x0; max_its = 100, opt_tol = 1e-6, rho = 0.9, mu = 1e-4, delta = 1e-8, BFGS = false)
    """
    p = Problem taken from Toms566 package
     p.x0 = standard initial guess
     p.obj = oracle returning objective function values
     p.grd = oracle returning gradient of obj
     p.hes = oracle returning hessian of obj
    x0 = starting point (if None, use p.x0)
    max_its = maximum number of iterations to try before quitting ( = 100 if not specified)
    opt_tol is tolerance defining the stopping condition |p.grd(x)| < opt_tol*|p.grd(x0)| ( = 1e-6 if not specified)
    rho = backtracking linesearch scaling constant
    mu = coefficient for Armijo condition
    delta = positive constant to replace negative (or zero) singular values of the Hessian
    TO DO:
        - add BFGS search direction option
    """
    x = x0; n = length(x0)
    f = p.obj(x0)
    g = p.grd(x0)
    g0 = p.grd(x0)
    its = 0
    count_notpd = 0
    if ~(BFGS)
        while (its < max_its) & (norm(g) > opt_tol * norm(g0)) # stopping criteria
            # compute function value, gradient, and hessian at current point
            f = p.obj(x)
            g = p.grd(x)
            H = p.hes(x)
            # try Cholesky factorization to determine if H is positive definite
            try R = chol(H)
                # if H is positive definite, compute the Newton search direction d = -H\g
                d = -H\g
                # use backtracking to compute an acceptable step length
                a = 1
                while p.obj(x+a*d) > f + a*mu*dot(g,d)
                    a = rho*a
                end
                # update x value using the step length a that we just decided on
                x = x + a*d
            catch
                count_notpd += 1
                # H is not positive definite, compute eigenvalue decomposition
                (l,Q) = eig(H)
                # flip and scale negative eigenvalues by delta > 0
                l = max(l,-delta*l)
                # compute search direction by inverting modified Hessian
                B = Q*diagm(l)*Q'
                d = -B\g
                a = 1
                while p.obj(x+a*d) > f + a*mu*dot(g,d)
                    a = rho*a
                end
                x = x + a*d
            end
            its += 1
        end
    else
        # Compute BFGS search direction
        # initialze B matrix to the identity
        B = eye(n)
        while (its < max_its) & (norm(g) > opt_tol * norm(g0))
            f = p.obj(x)
            g = p.grd(x)
            d = -B\g
            a = 1
            while p.obj(x+a*d) > f + mu*a*dot(d,g)
                a = a*rho
            end
            s = a*d
            x = x + s
            y = p.grd(x) - g
            # BFGS update
            B = B + y*y'/dot(y,s) - B*s*s'*B/dot(s,B*s)
            its += 1
        end
    end        
    return (x,its)
end

newtmin_tom (generic function with 1 method)

In [88]:
timeout = falses(18)
nanflags = falses(18)
for n = 1:18
    println("Solving problem ", n)
    p = Problem(n)
    (x,i) = newtmin_tom(p,p.x0,max_its = 500)
    if i == 500
        timeout[n] = true
    end
    if any(isnan([x;p.obj(x)]))
        nanflags[n] = true
    end
    println("    optimal x value is ",x)
    println("    numer of iterations is ",i)
    println("    minimum objective value is ",p.obj(x))
end

Solving problem 1
    optimal x value is [1.0,5.62177372484812e-15,9.079236389788476e-15]
    numer of iterations is 14
    minimum objective value is 8.417244260790461e-29
Solving problem 2
    optimal x value is [NaN,NaN,NaN,NaN,NaN,NaN]
    numer of iterations is 3
    minimum objective value is NaN
Solving problem 3
    optimal x value is [0.3989561378387567,1.0000190844878059,3.1362600217242657e-19]
    numer of iterations is 3
    minimum objective value is 1.1279327696191204e-8
Solving problem 4
    optimal x value is [2.0553054200738395e-6,48.654569307229515]
    numer of iterations is 14
    minimum objective value is 1.0415284933270543e-8
Solving problem 5
    optimal x value is [NaN,NaN,NaN]
    numer of iterations is 2
    minimum objective value is NaN
Solving problem 6
    optimal x value is [8.080843373914584,-13.331820046793583,-7.082525700438805,0.5370923145274692,-19.227015687379332,-10.183447082053197,-4.626454112678454,17.288792751336008,23.470558068177215,-8.034347

In [89]:
nanflags

18-element BitArray{1}:
 false
  true
 false
 false
  true
 false
 false
 false
 false
 false
 false
 false
 false
 false
 false
 false
 false
  true

# Problem 2

In [4]:
datafile = open("binary.csv")
admitdata = readcsv(datafile)
(M,N) = size(admitdata)
# M-1 = number of data points
# N = number of dimensions to each data point
# print(admitdata[1,:]) #read out column headers

# pack data into vectors
y = admitdata[2:M,1]
u = admitdata[2:M,2:3]
# define the expression for the negative log-likelihood function, which is what we wish to minimize. here x[1:2] = a, x[3] = beta
ex = :(L=0;
for k = 1:(M-1)
    L += -y[k]*(x[1]*u[k,1]+x[2]*u[k,2]+x[3]) + log(1+exp(x[1]*u[k,1]+x[2]*u[k,2]+x[3]))
end;
L)

quote 
    L = 0
    begin 
        for k = 1:M - 1 # In[4], line 14:
            L += -(y[k]) * (x[1] * u[k,1] + x[2] * u[k,2] + x[3]) + log(1 + exp(x[1] * u[k,1] + x[2] * u[k,2] + x[3]))
        end
        L
    end
end

In [52]:
dump(ex)

Expr 
  head: Symbol block
  args: Array(Any,(2,))
    1: Expr 
      head: Symbol =
      args: Array(Any,(2,))
        1: Symbol L
        2: Int32 0
      typ: Any
    2: Expr 
      head: Symbol block
      args: Array(Any,(2,))
        1: Expr 
          head: Symbol for
          args: Array(Any,(2,))
          typ: Any
        2: Symbol L
      typ: Any
  typ: Any


In [ ]:
# use ReverseDiffSource to get derivatives of ex
res = rdiff(ex, x = zeros(3), order = 2);

 in depwarn at deprecated.jl:73
 in evalsort! at C:\Users\Jordan\.julia\v0.4\ReverseDiffSource\src\graph.jl:295
 in simplify! at C:\Users\Jordan\.julia\v0.4\ReverseDiffSource\src\simplify.jl:12
 in rdiff at C:\Users\Jordan\.julia\v0.4\ReverseDiffSource\src\rdiff.jl:33
 in include_string at loading.jl:266
 in execute_request_0x535c5df2 at C:\Users\Jordan\.julia\v0.4\IJulia\src\execute_request.jl:177
 in eventloop at C:\Users\Jordan\.julia\v0.4\IJulia\src\IJulia.jl:141
 in anonymous at task.jl:447
while loading In[5], in expression starting on line 2
 in depwarn at deprecated.jl:73
 in evalsort! at C:\Users\Jordan\.julia\v0.4\ReverseDiffSource\src\graph.jl:295
 in simplify! at C:\Users\Jordan\.julia\v0.4\ReverseDiffSource\src\simplify.jl:12
 in rdiff at C:\Users\Jordan\.julia\v0.4\ReverseDiffSource\src\rdiff.jl:33
 in include_string at loading.jl:266
 in execute_request_0x535c5df2 at C:\Users\Jordan\.julia\v0.4\IJulia\src\execute_request.jl:177
 in eventloop at C:\Users\Jordan\.julia\v0.

In [38]:
function newtmin(f, derivs, x0; max_its = 100, opt_tol = 1e-6, rho = 0.9, mu = 1e-4, delta = 1e-8, BFGS = false)
    """
    f = objective function to be minimized
    g = gradient of f
    H = Hessian of f
    x0 = starting point (if None, use p.x0)
    max_its = maximum number of iterations to try before quitting ( = 100 if not specified)
    opt_tol is tolerance defining the stopping condition |p.grd(x)| < opt_tol*|p.grd(x0)| ( = 1e-6 if not specified)
    rho = backtracking linesearch scaling constant
    mu = coefficient for Armijo condition
    delta = positive constant to replace negative (or zero) singular values of the Hessian
    TO DO:
        - add BFGS search direction option
    """
    x = x0; n = length(x0)
    fk = f(x)
    (gk,Hk) = derivs(x)
    g0 = gk
    its = 0
    count_notpd = 0
    if ~(BFGS)
        while (its < max_its) & (norm(gk) > opt_tol * norm(g0)) # stopping criteria
            # compute function value, gradient, and hessian at current point
            fk = f(x)
            (gk,Hk) = derivs(x)
            # try Cholesky factorization to determine if H is positive definite
            try R = chol(Hk)
                # if H is positive definite, compute the Newton search direction d = -H\g
                d = -Hk\gk
                # use backtracking to compute an acceptable step length
                a = 1
                while f(x+a*d) >= fk + a*mu*dot(gk,d)
                    a = rho*a
                end
                # update x value using the step length a that we just decided on
                x = x + a*d
            catch
                count_notpd += 1
                # H is not positive definite, compute eigenvalue decomposition
                (l,Q) = eig(Hk)
                # flip and scale negative eigenvalues by delta > 0
                l = max(l,-delta*l)
                # compute search direction by inverting modified Hessian
                B = Q*diagm(l)*Q'
                d = -B\g
                a = 1
                while f(x+a*d) >= fk + a*mu*dot(gk,d)
                    a = rho*a
                end
                x = x + a*d
            end
            its += 1
        end
    else
        # Compute BFGS search direction
        # initialze B matrix to the identity
        B = eye(n)
        while (its < max_its) & (norm(gk) > opt_tol * norm(g0))
            fk = f(x)
            (gk,Hk) = derivs(x)
            d = -B\g
            a = 1
            while f(x+a*d) >= fk + mu*a*dot(d,gk)
                a = a*rho
            end
            s = a*d
            x = x + s
            y = g(x) - gk
            # BFGS update
            B = B + y*y'/dot(y,s) - B*s*s'*B/dot(s,B*s)
            its += 1
        end
    end        
    return (x,its,count_notpd)
end

newtmin (generic function with 2 methods)

In [40]:
@eval derivs(x) = $res[2:3]
@eval f(x) = $ex

f (generic function with 1 method)

In [64]:
newtmin(f,derivs,[0.,0.,0.],rho=0.5)

([0.002690683595964319,0.7546868559629355,-4.949378062622547],5,0)